# Homework Assignment 3

Save your assignment in your **mp248** repository, in **mp248/Assignments/hwk.3.ipynb**.  

The pre-grading script will offer feedback on problems P1, P2, P3 and P4.

Your assignment is due at **11:59pm** on **Friday November 15th**.

----

## P.1 - Crime stats

Construct a dictionary whose keys are the crime types, and whose values are lists (in descending order) of the five dates with the most crimes of that type. Only include crimes where there are **at least** five dates with ten or more occurances of that crime type. If two or more dates have the same number of crime records, sort them so that the earlier date appears first, i.e. Dec 10th 2014 would be before Jan 2nd 2015.  Print your dictionary with the **pprint** command.

**Hint:** There are only 6 crime types that meet the above criterion.

In [1]:
%cd ../../mp248-course

/home/user/mp248-course


In [2]:
#import cdat
from cdat import cDat

Crime database library.

Looking for vicpd.geojson in directory ./Data/
 modify the cdatfile and cdatloc variables in cdat.py appropriately
 if the file can not be found.

Complete records in cDat, incomplete records in bDat.



In [3]:
import collections as co
import pprint as pp
import operator as op
import calendar as cal

In [4]:
pp.pprint([cDat[x] for x in range(1)])

[{'ID': 760527874,
  'address': '1200 Block JOHNSON ST',
  'case_number': (16, 22918),
  'city': 'victoria',
  'coords': (-123.348998693722, 48.4255680718449),
  'cre_dt': datetime.datetime(2016, 5, 26, 9, 46, 43),
  'inc_dt': datetime.datetime(2016, 5, 25, 1, 29),
  'type': ('Disorder', 'CAUSE A DISTURBANCE'),
  'upd_dt': datetime.datetime(2016, 6, 23, 19, 40, 33)}]


In [5]:
print(type(cDat[0]))

<class 'dict'>


In [6]:
types = {c['type'] for c in cDat}
di = dict()
for typ in types:
    ctdict = co.defaultdict(int)
    for c in cDat:
        if c['type'] == typ:
            ctdict[c['inc_dt'].date()] += 1
    sorted_ctdict = sorted(list(ctdict.items()), key = op.itemgetter(1))[-1:-6:-1]     
    if sorted_ctdict[-1][1] > 9:
        di[typ] = sorted_ctdict 

In [7]:
pp.pprint(di)

{('Disorder', 'CAUSE A DISTURBANCE'): [(datetime.date(2014, 7, 6), 13),
                                       (datetime.date(2015, 4, 20), 11),
                                       (datetime.date(2015, 4, 18), 10),
                                       (datetime.date(2011, 7, 3), 10),
                                       (datetime.date(2014, 10, 5), 10)],
 ('Liquor', 'LIQUOR-INTOX IN PUBLIC PLACE'): [(datetime.date(2011, 7, 1), 44),
                                              (datetime.date(2013, 7, 1), 33),
                                              (datetime.date(2015, 7, 1), 28),
                                              (datetime.date(2012, 7, 1), 23),
                                              (datetime.date(2014, 7, 1), 21)],
 ('Other', 'BYLAW-NOISE'): [(datetime.date(2011, 10, 29), 16),
                            (datetime.date(2011, 7, 2), 16),
                            (datetime.date(2015, 10, 17), 14),
                            (datetime.date(2013, 5, 4

In [8]:
print("length =",len(di))

length = 7


In [9]:
pp.pprint(di['Theft', 'THEFT-OTHER UNDER $5000'])

[(datetime.date(2019, 8, 29), 15),
 (datetime.date(2019, 7, 30), 13),
 (datetime.date(2019, 6, 28), 12),
 (datetime.date(2013, 6, 6), 12),
 (datetime.date(2013, 4, 5), 12)]


----

## P.2 - Average crime locations.

Write a function that uses [spherical polar coordinates](https://en.wikipedia.org/wiki/Spherical_coordinate_system) to convert the **(longitude,latitude)** coordinate pairs into 3-dimensional Euclidean coordinates.  Compute the average location (in 3-dimensional space) of all the crime types in the **cdat.cDat** variable.  Invert your spherical polar coordinates, creating a dictionary indexed by crime types, returning the **(longitude,latitude)** pair of the average location for that crime type. Print your final dictionary using **pp.pprint**. 

**Note:** if you do not recall how longitude and latitude relate to spherical polar coordinates, read the above Wikipedia article carefully, together with the [longitude-latitude](https://en.wikipedia.org/wiki/Geographic_coordinate_system) page.

In [10]:
import numpy as np
import math as ma

In [11]:
def polar_to_cartesian(long, lat):
    '''
    Convert spherical polar coordinates to 3D Euclidean coordinates
    In this case, r = 1
    '''
    # lab x = rcos(lat)cos(long) vs wiki x = rsin(θ)cos(φ)
    # lab y = rcos(lat)sin(long) vs wiki y = rsin(θ)sin(φ)
    # lab z = rsin(lat) vs wiki z = rcos(θ)
    # θ = lat, φ = long
    # First: Convert degree to radians for numpy
    x = np.sin(ma.radians(lat))*np.cos(ma.radians(long))
    y = np.sin(ma.radians(lat))*np.sin(ma.radians(long))
    z = np.cos(ma.radians(lat))
    return(x, y, z)

def cartesian_to_polar(x_coords, y_coords, z_coords):
    '''
    Convert cartesian coordinates to spherical polar coordinates
    '''
    # θ = lat, φ = long
    r = 1
    lat = ma.degrees(np.arccos(z_coords/r))
    long = ma.degrees(np.arctan(y_coords/x_coords))
    if long > 0:
        long = -180 + long
    return(long, lat)

In [12]:
print("(-123.35_, 48.43_) ->",polar_to_cartesian(-123.348998693722, 48.4255680718449))
print("->",cartesian_to_polar(-0.41125540309882863, -0.6249112431808368, 0.6635924438751551))

(-123.35_, 48.43_) -> (-0.41125540309882863, -0.6249112431808368, 0.6635924438751551)
-> (-123.348998693722, 48.4255680718449)


In [13]:
dict2 = dict()
## For each type of crimes, take (lat, long), convert to Cartesian
## Then take the avg of each x,y,z coords by sum/(#num of crimes)
## Convert back to polar. Return a dictionary of avg polar.
for typ in types:
    sum_x = 0
    sum_y = 0
    sum_z = 0
    total_crime_count = 0
    ctdict = co.defaultdict(int)
    for c in cDat:
        if c['type'] == typ:
            ctdict[c['coords']] += 1
    for i in ctdict.items():
        lat1 = i[0][0]
        long1 = i[0][1]
        crime_count = i[1]
        x, y, z = polar_to_cartesian(lat1, long1)
        #print(i[0])
        #print(x,y,z)
        total_crime_count += crime_count
        sum_x += x
        sum_y += y
        sum_z += z 
    avg_coords = (sum_x/ total_crime_count, sum_y/total_crime_count, sum_z/total_crime_count)
    dict2[typ] = cartesian_to_polar(avg_coords[0], avg_coords[1],avg_coords[2])

In [14]:
pp.pprint(dict2)

{('Alarm', 'FALSE ALARMS'): (-123.36669657827778, 63.72855910561595),
 ('Arson', 'ARSON-DISREGARD FOR HUMAN LIFE'): (-123.36434309858242,
                                               54.50985805480552),
 ('Arson', 'ARSON-PROPERTY'): (-123.36835002189386, 51.59940406949776),
 ('Assault', 'ASSAULT AGAINST POLICE OFFICER'): (-123.36720488648099,
                                                 56.77419339232461),
 ('Assault', 'ASSAULT-COMMON OR TRESPASS'): (-123.3697481856791,
                                             73.12474744226293),
 ('Assault', 'ASSAULTS-OTHER'): (-123.36845048912659, 58.23153330122856),
 ('Assault with Deadly Weapon', 'ASSAULT OT P/O-W/WPN OR CBH'): (-123.36635892685001,
                                                                 54.81660656340022),
 ('Assault with Deadly Weapon', 'ASSAULT POLICE-W/WEAPON OR CBH'): (-123.36700827186367,
                                                                    50.9239546782655),
 ('Assault with Deadly Weapon', '

----

## P.3 - Crime + Weather data

Load the crime and weather data, i.e. the **cdat.py** and **wdat.py** libraries.

Determine the set of days where we have crime data and weather data, specifically.

1. Dates where we have crime reports in our **cDat** variable.
2. Dates with crime reports and the max/min/mean temperature readings for Victoria in **wdat**. 
3. Dates with crime reports and the max/min/mean temperature readings and the Rain/Precipitation/Snow totals.

Let the number of elements of (1) be **CDD**.  The number of elements of (2) as **CDTD**.  The number of elements of (3) as **CDTPD**,
then execute the command below.

`print(CDD, 'crime data days', CDTD, 'crime data + temp days', CDTPD, 'crime data + precipitation + temp days')`


In [15]:
%cd Assignments/

/home/user/mp248-course/Assignments


In [16]:
#import wdat as wDat
from wdat import mdat

wdat.py looking in: /home/user/mp248-course/Assignments/../Data/CWD/
 for CHWD .csv files. Correct the 'route' variable if needed.
Transport Canada codes for each city: 
defaultdict(<class 'set'>,
            {'w.cal': {'YYC'},
             'w.edm': {'YEG'},
             'w.sask': {'POX', 'YXE'},
             'w.vic': {'YYJ'}})
Weather data loaded. 71588 records, total.


In [42]:
##pp.pprint([c for c in mdat.items() if 'w.vic' in c[0] ])

In [43]:
##pp.pprint([c for c in mdat.items() if 'Data Quality' in c[1]])

In [47]:
## All inc_dt from cDat
c_date = [e['inc_dt'].date() for e in cDat]
#pp.pprint(c_date)

In [46]:
## All weather data in Victoria that has the same dates as in c_date
CDD = [c for c in mdat.items() if ('w.vic' in c[0]) and (c[0][1] in c_date)]
pp.pprint(CDD)

[(('w.vic', datetime.date(2013, 1, 1)), {'Data Quality': '‡'}),
 (('w.vic', datetime.date(2013, 1, 2)), {'Data Quality': '‡'}),
 (('w.vic', datetime.date(2013, 1, 3)), {'Data Quality': '‡'}),
 (('w.vic', datetime.date(2013, 1, 4)), {'Data Quality': '‡'}),
 (('w.vic', datetime.date(2013, 1, 5)), {'Data Quality': '‡'}),
 (('w.vic', datetime.date(2013, 1, 6)), {'Data Quality': '‡'}),
 (('w.vic', datetime.date(2013, 1, 7)), {'Data Quality': '‡'}),
 (('w.vic', datetime.date(2013, 1, 8)), {'Data Quality': '‡'}),
 (('w.vic', datetime.date(2013, 1, 9)), {'Data Quality': '‡'}),
 (('w.vic', datetime.date(2013, 1, 10)), {'Data Quality': '‡'}),
 (('w.vic', datetime.date(2013, 1, 11)), {'Data Quality': '‡'}),
 (('w.vic', datetime.date(2013, 1, 12)), {'Data Quality': '‡'}),
 (('w.vic', datetime.date(2013, 1, 13)), {'Data Quality': '‡'}),
 (('w.vic', datetime.date(2013, 1, 14)), {'Data Quality': '‡'}),
 (('w.vic', datetime.date(2013, 1, 15)), {'Data Quality': '‡'}),
 (('w.vic', datetime.date(2013, 1,

   'Max Temp (°C)': 21.4,
   'Mean Temp (°C)': 17.8,
   'Min Temp (°C)': 14.2,
   'Spd of Max Gust (km/h)': '<31',
   'Total Precip (mm)': 1.6,
   'Total Rain (mm)': 1.6,
   'Total Snow (cm)': 0.0}),
 (('w.vic', datetime.date(2013, 8, 29)),
  {'Cool Deg Days (°C)': '0.0',
   'Data Quality': '‡',
   'Heat Deg Days (°C)': '1.9',
   'Max Temp (°C)': 18.6,
   'Mean Temp (°C)': 16.1,
   'Min Temp (°C)': 13.6,
   'Spd of Max Gust (km/h)': '<31',
   'Total Precip (mm)': 10.0,
   'Total Rain (mm)': 10.0,
   'Total Snow (cm)': 0.0}),
 (('w.vic', datetime.date(2013, 8, 30)),
  {'Cool Deg Days (°C)': '0.0',
   'Data Quality': '‡',
   'Dir of Max Gust (10s deg)': '24',
   'Heat Deg Days (°C)': '0.2',
   'Max Temp (°C)': 22.2,
   'Mean Temp (°C)': 17.8,
   'Min Temp (°C)': 13.4,
   'Spd of Max Gust (km/h)': '44',
   'Total Precip (mm)': 6.2,
   'Total Rain (mm)': 6.2,
   'Total Snow (cm)': 0.0}),
 (('w.vic', datetime.date(2013, 8, 31)),
  {'Cool Deg Days (°C)': '0.7',
   'Data Quality': '‡',
   'He

   'Total Snow (cm)': 0.0}),
 (('w.vic', datetime.date(2013, 10, 17)),
  {'Cool Deg Days (°C)': '0.0',
   'Data Quality': '‡',
   'Heat Deg Days (°C)': '9.3',
   'Max Temp (°C)': 13.6,
   'Mean Temp (°C)': 8.7,
   'Min Temp (°C)': 3.7,
   'Spd of Max Gust (km/h)': '<31',
   'Total Precip (mm)': 0.0,
   'Total Rain (mm)': 0.0,
   'Total Snow (cm)': 0.0}),
 (('w.vic', datetime.date(2013, 10, 18)), {'Data Quality': '‡'}),
 (('w.vic', datetime.date(2013, 10, 19)), {'Data Quality': '‡'}),
 (('w.vic', datetime.date(2013, 10, 20)),
  {'Cool Deg Days (°C)': '0.0',
   'Data Quality': '‡',
   'Heat Deg Days (°C)': '8.9',
   'Max Temp (°C)': 9.9,
   'Mean Temp (°C)': 9.1,
   'Min Temp (°C)': 8.3,
   'Spd of Max Gust (km/h)': '<31',
   'Total Precip (mm)': 0.0,
   'Total Rain (mm)': 0.0,
   'Total Snow (cm)': 0.0}),
 (('w.vic', datetime.date(2013, 10, 21)),
  {'Cool Deg Days (°C)': '0.0',
   'Data Quality': '‡',
   'Heat Deg Days (°C)': '8.4',
   'Max Temp (°C)': 11.4,
   'Mean Temp (°C)': 9.6,
  

   'Data Quality': '‡',
   'Dir of Max Gust Flag': 'M',
   'Heat Deg Days (°C)': '17.5',
   'Heat Deg Days Flag': 'E',
   'Max Temp (°C)': 3.2,
   'Mean Temp (°C)': 0.5,
   'Mean Temp Flag': 'E',
   'Min Temp (°C)': -2.3,
   'Min Temp Flag': 'E',
   'Spd of Max Gust Flag': 'M',
   'Total Precip (mm)': 4.0,
   'Total Precip Flag': 'E',
   'Total Rain Flag': 'M',
   'Total Snow Flag': 'M'}),
 (('w.vic', datetime.date(2013, 12, 20)),
  {'Cool Deg Days (°C)': '0.0',
   'Data Quality': '‡',
   'Dir of Max Gust (10s deg)': '12',
   'Heat Deg Days (°C)': '16.7',
   'Max Temp (°C)': 2.4,
   'Mean Temp (°C)': 1.3,
   'Min Temp (°C)': 0.2,
   'Snow on Grnd (cm)': '4',
   'Spd of Max Gust (km/h)': '37',
   'Total Precip (mm)': 18.8,
   'Total Rain (mm)': 7.0,
   'Total Snow (cm)': 11.8}),
 (('w.vic', datetime.date(2013, 12, 21)),
  {'Cool Deg Days (°C)': '0.0',
   'Data Quality': '‡',
   'Heat Deg Days (°C)': '14.9',
   'Max Temp (°C)': 4.5,
   'Mean Temp (°C)': 3.1,
   'Min Temp (°C)': 1.7,
   '

 (('w.vic', datetime.date(2017, 3, 3)),
  {'Cool Deg Days (°C)': '0.0',
   'Data Quality': '‡',
   'Dir of Max Gust (10s deg)': '16',
   'Heat Deg Days (°C)': '12.6',
   'Max Temp (°C)': 8.0,
   'Mean Temp (°C)': 5.4,
   'Min Temp (°C)': 2.7,
   'Spd of Max Gust (km/h)': '50',
   'Total Precip (mm)': 7.6,
   'Total Rain (mm)': 7.6,
   'Total Snow (cm)': 0.0}),
 (('w.vic', datetime.date(2017, 3, 4)),
  {'Cool Deg Days (°C)': '0.0',
   'Data Quality': '‡',
   'Dir of Max Gust (10s deg)': '26',
   'Heat Deg Days (°C)': '15.7',
   'Max Temp (°C)': 6.2,
   'Mean Temp (°C)': 2.3,
   'Min Temp (°C)': -1.7,
   'Spd of Max Gust (km/h)': '39',
   'Total Precip (mm)': 0.0,
   'Total Rain (mm)': 0.0,
   'Total Snow (cm)': 0.0}),
 (('w.vic', datetime.date(2017, 3, 5)),
  {'Cool Deg Days (°C)': '0.0',
   'Data Quality': '‡',
   'Dir of Max Gust (10s deg)': '5',
   'Heat Deg Days (°C)': '15.9',
   'Max Temp (°C)': 4.6,
   'Mean Temp (°C)': 2.1,
   'Min Temp (°C)': -0.4,
   'Snow on Grnd (cm)': '2',
 

...

   'Total Snow (cm)': 0.0}),
 (('w.vic', datetime.date(2012, 4, 6)),
  {'Cool Deg Days (°C)': '0.0',
   'Heat Deg Days (°C)': '13.2',
   'Max Temp (°C)': 10.1,
   'Mean Temp (°C)': 4.8,
   'Min Temp (°C)': -0.6,
   'Snow on Grnd (cm)': '0',
   'Spd of Max Gust (km/h)': '<31',
   'Total Precip (mm)': 0.0,
   'Total Precip Flag': 'T',
   'Total Rain (mm)': 0.0,
   'Total Rain Flag': 'T',
   'Total Snow (cm)': 0.0}),
 (('w.vic', datetime.date(2012, 4, 7)),
  {'Cool Deg Days (°C)': '0.0',
   'Heat Deg Days (°C)': '11.8',
   'Max Temp (°C)': 13.3,
   'Mean Temp (°C)': 6.2,
   'Min Temp (°C)': -0.9,
   'Snow on Grnd (cm)': '0',
   'Spd of Max Gust (km/h)': '<31',
   'Total Precip (mm)': 0.0,
   'Total Rain (mm)': 0.0,
   'Total Snow (cm)': 0.0}),
 (('w.vic', datetime.date(2012, 4, 8)),
  {'Cool Deg Days (°C)': '0.0',
   'Heat Deg Days (°C)': '9.3',
   'Max Temp (°C)': 15.7,
   'Mean Temp (°C)': 8.7,
   'Min Temp (°C)': 1.7,
   'Snow on Grnd (cm)': '0',
   'Spd of Max Gust (km/h)': '<31',
   

   'Total Precip (mm)': 0.0,
   'Total Rain (mm)': 0.0,
   'Total Snow (cm)': 0.0}),
 (('w.vic', datetime.date(2012, 6, 11)),
  {'Cool Deg Days (°C)': '0.0',
   'Heat Deg Days (°C)': '4.2',
   'Max Temp (°C)': 20.3,
   'Mean Temp (°C)': 13.8,
   'Min Temp (°C)': 7.2,
   'Snow on Grnd (cm)': '0',
   'Spd of Max Gust (km/h)': '<31',
   'Total Precip (mm)': 0.0,
   'Total Precip Flag': 'T',
   'Total Rain (mm)': 0.0,
   'Total Rain Flag': 'T',
   'Total Snow (cm)': 0.0}),
 (('w.vic', datetime.date(2012, 6, 12)),
  {'Cool Deg Days (°C)': '0.0',
   'Heat Deg Days (°C)': '3.5',
   'Max Temp (°C)': 16.6,
   'Mean Temp (°C)': 14.5,
   'Min Temp (°C)': 12.4,
   'Snow on Grnd (cm)': '0',
   'Spd of Max Gust (km/h)': '<31',
   'Total Precip (mm)': 0.0,
   'Total Precip Flag': 'T',
   'Total Rain (mm)': 0.0,
   'Total Rain Flag': 'T',
   'Total Snow (cm)': 0.0}),
 (('w.vic', datetime.date(2012, 6, 13)),
  {'Cool Deg Days (°C)': '0.0',
   'Heat Deg Days (°C)': '3.8',
   'Max Temp (°C)': 17.7,
   'M

   'Heat Deg Days (°C)': '1.0',
   'Max Temp (°C)': 21.4,
   'Mean Temp (°C)': 17.0,
   'Min Temp (°C)': 12.5,
   'Snow on Grnd (cm)': '0',
   'Spd of Max Gust (km/h)': '<31',
   'Total Precip (mm)': 0.0,
   'Total Rain (mm)': 0.0,
   'Total Snow (cm)': 0.0}),
 (('w.vic', datetime.date(2012, 8, 23)),
  {'Cool Deg Days (°C)': '0.0',
   'Heat Deg Days (°C)': '1.8',
   'Max Temp (°C)': 20.3,
   'Mean Temp (°C)': 16.2,
   'Min Temp (°C)': 12.1,
   'Snow on Grnd (cm)': '0',
   'Spd of Max Gust (km/h)': '<31',
   'Total Precip (mm)': 0.0,
   'Total Precip Flag': 'T',
   'Total Rain (mm)': 0.0,
   'Total Rain Flag': 'T',
   'Total Snow (cm)': 0.0}),
 (('w.vic', datetime.date(2012, 8, 24)),
  {'Cool Deg Days (°C)': '0.0',
   'Heat Deg Days (°C)': '3.0',
   'Max Temp (°C)': 19.9,
   'Mean Temp (°C)': 15.0,
   'Min Temp (°C)': 10.1,
   'Snow on Grnd (cm)': '0',
   'Spd of Max Gust (km/h)': '<31',
   'Total Precip (mm)': 0.0,
   'Total Rain (mm)': 0.0,
   'Total Snow (cm)': 0.0}),
 (('w.vic', dat

   'Total Snow (cm)': 0.0}),
 (('w.vic', datetime.date(2012, 10, 29)),
  {'Cool Deg Days (°C)': '0.0',
   'Dir of Max Gust (10s deg)': '21',
   'Dir of Max Gust Flag': 'E',
   'Heat Deg Days (°C)': '5.7',
   'Max Temp (°C)': 15.2,
   'Mean Temp (°C)': 12.3,
   'Min Temp (°C)': 9.3,
   'Snow on Grnd (cm)': '0',
   'Spd of Max Gust (km/h)': '50',
   'Spd of Max Gust Flag': 'E',
   'Total Precip (mm)': 15.5,
   'Total Rain (mm)': 15.5,
   'Total Snow (cm)': 0.0}),
 (('w.vic', datetime.date(2012, 10, 30)),
  {'Cool Deg Days (°C)': '0.0',
   'Dir of Max Gust (10s deg)': '4',
   'Dir of Max Gust Flag': 'E',
   'Heat Deg Days (°C)': '6.8',
   'Max Temp (°C)': 12.3,
   'Mean Temp (°C)': 11.2,
   'Min Temp (°C)': 10.0,
   'Snow on Grnd (cm)': '0',
   'Spd of Max Gust (km/h)': '32',
   'Spd of Max Gust Flag': 'E',
   'Total Precip (mm)': 29.8,
   'Total Rain (mm)': 29.8,
   'Total Snow (cm)': 0.0}),
 (('w.vic', datetime.date(2012, 10, 31)),
  {'Cool Deg Days (°C)': '0.0',
   'Heat Deg Days (°C)'

   'Mean Temp (°C)': 2.7,
   'Min Temp (°C)': 0.0,
   'Snow on Grnd (cm)': '0',
   'Spd of Max Gust (km/h)': '<31',
   'Total Precip (mm)': 0.0,
   'Total Rain (mm)': 0.0,
   'Total Snow (cm)': 0.0}),
 (('w.vic', datetime.date(2012, 12, 31)),
  {'Cool Deg Days (°C)': '0.0',
   'Heat Deg Days (°C)': '15.1',
   'Max Temp (°C)': 3.7,
   'Mean Temp (°C)': 2.9,
   'Min Temp (°C)': 2.1,
   'Snow on Grnd (cm)': '0',
   'Spd of Max Gust (km/h)': '<31',
   'Total Precip (mm)': 4.3,
   'Total Rain (mm)': 4.3,
   'Total Snow (cm)': 0.0})]


In [50]:
## Dates with crime reports and the max/min/mean temperature readings for Victoria in wdat.
CDTD = [cd for cd in CDD if ('Max Temp (°C)' and 'Mean Temp (°C)' and 'Min Temp (°C)') in cd[1] ]
pp.pprint(CDTD)

[(('w.vic', datetime.date(2013, 7, 11)),
  {'Cool Deg Days (°C)': '0.0',
   'Data Quality': '‡',
   'Dir of Max Gust (10s deg)': '25',
   'Heat Deg Days (°C)': '1.6',
   'Max Temp (°C)': 20.9,
   'Mean Temp (°C)': 16.4,
   'Min Temp (°C)': 11.9,
   'Spd of Max Gust (km/h)': '37',
   'Total Precip (mm)': 0.0,
   'Total Rain (mm)': 0.0,
   'Total Snow (cm)': 0.0}),
 (('w.vic', datetime.date(2013, 7, 12)),
  {'Cool Deg Days (°C)': '0.0',
   'Data Quality': '‡',
   'Dir of Max Gust (10s deg)': '13',
   'Heat Deg Days (°C)': '2.0',
   'Max Temp (°C)': 21.2,
   'Mean Temp (°C)': 16.0,
   'Min Temp (°C)': 10.7,
   'Spd of Max Gust (km/h)': '33',
   'Total Precip (mm)': 0.0,
   'Total Rain (mm)': 0.0,
   'Total Snow (cm)': 0.0}),
 (('w.vic', datetime.date(2013, 7, 13)),
  {'Cool Deg Days (°C)': '0.0',
   'Data Quality': '‡',
   'Dir of Max Gust (10s deg)': '15',
   'Heat Deg Days (°C)': '1.8',
   'Max Temp (°C)': 22.9,
   'Mean Temp (°C)': 16.2,
   'Min Temp (°C)': 9.5,
   'Spd of Max Gust (km

   'Mean Temp (°C)': 16.4,
   'Min Temp (°C)': 10.8,
   'Spd of Max Gust (km/h)': '<31',
   'Total Precip (mm)': 0.0,
   'Total Rain (mm)': 0.0,
   'Total Snow (cm)': 0.0}),
 (('w.vic', datetime.date(2013, 9, 10)),
  {'Cool Deg Days (°C)': '0.0',
   'Data Quality': '‡',
   'Heat Deg Days (°C)': '0.6',
   'Max Temp (°C)': 23.9,
   'Mean Temp (°C)': 17.4,
   'Min Temp (°C)': 10.9,
   'Spd of Max Gust (km/h)': '<31',
   'Total Precip (mm)': 0.0,
   'Total Rain (mm)': 0.0,
   'Total Snow (cm)': 0.0}),
 (('w.vic', datetime.date(2013, 9, 11)),
  {'Cool Deg Days (°C)': '4.1',
   'Data Quality': '‡',
   'Heat Deg Days (°C)': '0.0',
   'Max Temp (°C)': 30.7,
   'Mean Temp (°C)': 22.1,
   'Min Temp (°C)': 13.5,
   'Spd of Max Gust (km/h)': '<31',
   'Total Precip (mm)': 0.0,
   'Total Rain (mm)': 0.0,
   'Total Snow (cm)': 0.0}),
 (('w.vic', datetime.date(2013, 9, 12)),
  {'Cool Deg Days (°C)': '0.0',
   'Data Quality': '‡',
   'Heat Deg Days (°C)': '0.7',
   'Max Temp (°C)': 22.4,
   'Mean Temp

   'Mean Temp (°C)': 9.2,
   'Min Temp (°C)': 6.4,
   'Spd of Max Gust (km/h)': '41',
   'Total Precip (mm)': 16.0,
   'Total Rain (mm)': 16.0,
   'Total Snow (cm)': 0.0}),
 (('w.vic', datetime.date(2013, 11, 8)),
  {'Cool Deg Days (°C)': '0.0',
   'Data Quality': '‡',
   'Heat Deg Days (°C)': '9.4',
   'Max Temp (°C)': 12.6,
   'Mean Temp (°C)': 8.6,
   'Min Temp (°C)': 4.5,
   'Spd of Max Gust (km/h)': '<31',
   'Total Precip (mm)': 0.0,
   'Total Rain (mm)': 0.0,
   'Total Snow (cm)': 0.0}),
 (('w.vic', datetime.date(2013, 11, 9)),
  {'Cool Deg Days (°C)': '0.0',
   'Data Quality': '‡',
   'Heat Deg Days (°C)': '11.9',
   'Max Temp (°C)': 9.1,
   'Mean Temp (°C)': 6.1,
   'Min Temp (°C)': 3.0,
   'Spd of Max Gust (km/h)': '<31',
   'Total Precip (mm)': 0.2,
   'Total Rain (mm)': 0.2,
   'Total Snow (cm)': 0.0}),
 (('w.vic', datetime.date(2013, 11, 10)),
  {'Cool Deg Days (°C)': '0.0',
   'Data Quality': '‡',
   'Heat Deg Days (°C)': '9.9',
   'Max Temp (°C)': 9.7,
   'Mean Temp (°C)

   'Total Snow (cm)': 0.0}),
 (('w.vic', datetime.date(2017, 1, 1)),
  {'Cool Deg Days (°C)': '0.0',
   'Data Quality': '‡',
   'Dir of Max Gust (10s deg)': '2',
   'Heat Deg Days (°C)': '16.3',
   'Max Temp (°C)': 4.9,
   'Mean Temp (°C)': 1.7,
   'Min Temp (°C)': -1.6,
   'Spd of Max Gust (km/h)': '54',
   'Total Precip (mm)': 1.4,
   'Total Rain (mm)': 1.4,
   'Total Snow (cm)': 0.0}),
 (('w.vic', datetime.date(2017, 1, 2)),
  {'Cool Deg Days (°C)': '0.0',
   'Data Quality': '‡',
   'Dir of Max Gust (10s deg)': '2',
   'Heat Deg Days (°C)': '17.9',
   'Max Temp (°C)': 1.3,
   'Mean Temp (°C)': 0.1,
   'Min Temp (°C)': -1.2,
   'Spd of Max Gust (km/h)': '61',
   'Total Precip (mm)': 0.0,
   'Total Rain (mm)': 0.0,
   'Total Snow (cm)': 0.0}),
 (('w.vic', datetime.date(2017, 1, 3)),
  {'Cool Deg Days (°C)': '0.0',
   'Data Quality': '‡',
   'Dir of Max Gust (10s deg)': '6',
   'Heat Deg Days (°C)': '18.9',
   'Max Temp (°C)': 0.5,
   'Mean Temp (°C)': -0.9,
   'Min Temp (°C)': -2.3,
 

   'Min Temp (°C)': 4.7,
   'Spd of Max Gust (km/h)': '50',
   'Total Precip (mm)': 5.6,
   'Total Rain (mm)': 5.6,
   'Total Snow (cm)': 0.0}),
 (('w.vic', datetime.date(2017, 2, 20)),
  {'Cool Deg Days (°C)': '0.0',
   'Data Quality': '‡',
   'Heat Deg Days (°C)': '13.1',
   'Max Temp (°C)': 8.1,
   'Mean Temp (°C)': 4.9,
   'Min Temp (°C)': 1.7,
   'Spd of Max Gust (km/h)': '<31',
   'Total Precip (mm)': 0.0,
   'Total Precip Flag': 'T',
   'Total Rain (mm)': 0.0,
   'Total Rain Flag': 'T',
   'Total Snow (cm)': 0.0}),
 (('w.vic', datetime.date(2017, 2, 21)),
  {'Cool Deg Days (°C)': '0.0',
   'Data Quality': '‡',
   'Dir of Max Gust (10s deg)': '26',
   'Heat Deg Days (°C)': '12.7',
   'Max Temp (°C)': 8.9,
   'Mean Temp (°C)': 5.3,
   'Min Temp (°C)': 1.6,
   'Spd of Max Gust (km/h)': '32',
   'Total Precip (mm)': 0.0,
   'Total Rain (mm)': 0.0,
   'Total Snow (cm)': 0.0}),
 (('w.vic', datetime.date(2017, 2, 22)),
  {'Cool Deg Days (°C)': '0.0',
   'Data Quality': '‡',
   'Heat De

...

   'Dir of Max Gust (10s deg)': '14',
   'Dir of Max Gust Flag': 'E',
   'Heat Deg Days (°C)': '8.7',
   'Max Temp (°C)': 14.2,
   'Mean Temp (°C)': 9.3,
   'Min Temp (°C)': 4.3,
   'Snow on Grnd (cm)': '0',
   'Spd of Max Gust (km/h)': '33',
   'Spd of Max Gust Flag': 'E',
   'Total Precip (mm)': 0.0,
   'Total Rain (mm)': 0.0,
   'Total Snow (cm)': 0.0}),
 (('w.vic', datetime.date(2012, 5, 19)),
  {'Cool Deg Days (°C)': '0.0',
   'Heat Deg Days (°C)': '7.4',
   'Max Temp (°C)': 17.7,
   'Mean Temp (°C)': 10.6,
   'Min Temp (°C)': 3.4,
   'Snow on Grnd (cm)': '0',
   'Spd of Max Gust (km/h)': '<31',
   'Total Precip (mm)': 0.0,
   'Total Rain (mm)': 0.0,
   'Total Snow (cm)': 0.0}),
 (('w.vic', datetime.date(2012, 5, 20)),
  {'Cool Deg Days (°C)': '0.0',
   'Heat Deg Days (°C)': '5.6',
   'Max Temp (°C)': 14.7,
   'Mean Temp (°C)': 12.4,
   'Min Temp (°C)': 10.0,
   'Snow on Grnd (cm)': '0',
   'Spd of Max Gust (km/h)': '<31',
   'Total Precip (mm)': 0.0,
   'Total Precip Flag': 'T',


   'Heat Deg Days (°C)': '0.1',
   'Max Temp (°C)': 25.0,
   'Mean Temp (°C)': 17.9,
   'Min Temp (°C)': 10.7,
   'Snow on Grnd (cm)': '0',
   'Spd of Max Gust (km/h)': '<31',
   'Total Precip (mm)': 0.0,
   'Total Rain (mm)': 0.0,
   'Total Snow (cm)': 0.0}),
 (('w.vic', datetime.date(2012, 7, 13)),
  {'Cool Deg Days (°C)': '0.0',
   'Dir of Max Gust (10s deg)': '12',
   'Dir of Max Gust Flag': 'E',
   'Heat Deg Days (°C)': '0.0',
   'Max Temp (°C)': 22.9,
   'Mean Temp (°C)': 18.0,
   'Min Temp (°C)': 13.0,
   'Snow on Grnd (cm)': '0',
   'Spd of Max Gust (km/h)': '50',
   'Spd of Max Gust Flag': 'E',
   'Total Precip (mm)': 3.0,
   'Total Rain (mm)': 3.0,
   'Total Snow (cm)': 0.0}),
 (('w.vic', datetime.date(2012, 7, 14)),
  {'Cool Deg Days (°C)': '0.3',
   'Heat Deg Days (°C)': '0.0',
   'Max Temp (°C)': 24.3,
   'Mean Temp (°C)': 18.3,
   'Min Temp (°C)': 12.3,
   'Snow on Grnd (cm)': '0',
   'Spd of Max Gust (km/h)': '<31',
   'Total Precip (mm)': 0.0,
   'Total Rain (mm)': 0.0,

  {'Cool Deg Days (°C)': '0.0',
   'Heat Deg Days (°C)': '3.0',
   'Max Temp (°C)': 19.9,
   'Mean Temp (°C)': 15.0,
   'Min Temp (°C)': 10.1,
   'Snow on Grnd (cm)': '0',
   'Spd of Max Gust (km/h)': '<31',
   'Total Precip (mm)': 0.0,
   'Total Rain (mm)': 0.0,
   'Total Snow (cm)': 0.0}),
 (('w.vic', datetime.date(2012, 8, 25)),
  {'Cool Deg Days (°C)': '0.0',
   'Heat Deg Days (°C)': '1.5',
   'Max Temp (°C)': 23.9,
   'Mean Temp (°C)': 16.5,
   'Min Temp (°C)': 9.1,
   'Snow on Grnd (cm)': '0',
   'Spd of Max Gust (km/h)': '<31',
   'Total Precip (mm)': 0.0,
   'Total Rain (mm)': 0.0,
   'Total Snow (cm)': 0.0}),
 (('w.vic', datetime.date(2012, 8, 26)),
  {'Cool Deg Days (°C)': '0.0',
   'Heat Deg Days (°C)': '3.8',
   'Max Temp (°C)': 18.2,
   'Mean Temp (°C)': 14.2,
   'Min Temp (°C)': 10.2,
   'Snow on Grnd (cm)': '0',
   'Spd of Max Gust (km/h)': '<31',
   'Total Precip (mm)': 0.2,
   'Total Rain (mm)': 0.2,
   'Total Snow (cm)': 0.0}),
 (('w.vic', datetime.date(2012, 8, 27)),

   'Min Temp (°C)': 5.9,
   'Snow on Grnd (cm)': '0',
   'Spd of Max Gust (km/h)': '<31',
   'Total Precip (mm)': 4.4,
   'Total Rain (mm)': 4.4,
   'Total Snow (cm)': 0.0}),
 (('w.vic', datetime.date(2012, 10, 24)),
  {'Cool Deg Days (°C)': '0.0',
   'Dir of Max Gust (10s deg)': '5',
   'Dir of Max Gust Flag': 'E',
   'Heat Deg Days (°C)': '10.9',
   'Max Temp (°C)': 9.0,
   'Mean Temp (°C)': 7.1,
   'Min Temp (°C)': 5.2,
   'Snow on Grnd (cm)': '0',
   'Spd of Max Gust (km/h)': '39',
   'Spd of Max Gust Flag': 'E',
   'Total Precip (mm)': 3.8,
   'Total Rain (mm)': 3.8,
   'Total Snow (cm)': 0.0}),
 (('w.vic', datetime.date(2012, 10, 25)),
  {'Cool Deg Days (°C)': '0.0',
   'Heat Deg Days (°C)': '10.1',
   'Max Temp (°C)': 10.6,
   'Mean Temp (°C)': 7.9,
   'Min Temp (°C)': 5.1,
   'Snow on Grnd (cm)': '0',
   'Spd of Max Gust (km/h)': '<31',
   'Total Precip (mm)': 0.0,
   'Total Rain (mm)': 0.0,
   'Total Snow (cm)': 0.0}),
 (('w.vic', datetime.date(2012, 10, 26)),
  {'Cool Deg Day

  {'Cool Deg Days (°C)': '0.0',
   'Heat Deg Days (°C)': '13.7',
   'Max Temp (°C)': 6.6,
   'Mean Temp (°C)': 4.3,
   'Min Temp (°C)': 1.9,
   'Snow on Grnd (cm)': '0',
   'Spd of Max Gust (km/h)': '<31',
   'Total Precip (mm)': 0.4,
   'Total Rain (mm)': 0.4,
   'Total Snow (cm)': 0.0}),
 (('w.vic', datetime.date(2012, 12, 28)),
  {'Cool Deg Days (°C)': '0.0',
   'Heat Deg Days (°C)': '13.0',
   'Max Temp (°C)': 6.6,
   'Mean Temp (°C)': 5.0,
   'Min Temp (°C)': 3.3,
   'Snow on Grnd (cm)': '0',
   'Spd of Max Gust (km/h)': '<31',
   'Total Precip (mm)': 2.2,
   'Total Rain (mm)': 2.2,
   'Total Snow (cm)': 0.0}),
 (('w.vic', datetime.date(2012, 12, 29)),
  {'Cool Deg Days (°C)': '0.0',
   'Heat Deg Days (°C)': '13.2',
   'Max Temp (°C)': 5.5,
   'Mean Temp (°C)': 4.8,
   'Min Temp (°C)': 4.0,
   'Snow on Grnd (cm)': '0',
   'Spd of Max Gust (km/h)': '<31',
   'Total Precip (mm)': 2.8,
   'Total Rain (mm)': 2.8,
   'Total Snow (cm)': 0.0}),
 (('w.vic', datetime.date(2012, 12, 30)),
 

In [51]:
##Dates with crime reports and the max/min/mean temperature readings and the Rain/Precipitation/Snow totals.
CDTPD = [cdt for cdt in CDTD if ('Total Precip (mm)' and 'Total Rain (mm)' and 'Total Snow (cm)') in cdt[1]]
pp.pprint(CDTPD)

[(('w.vic', datetime.date(2013, 7, 11)),
  {'Cool Deg Days (°C)': '0.0',
   'Data Quality': '‡',
   'Dir of Max Gust (10s deg)': '25',
   'Heat Deg Days (°C)': '1.6',
   'Max Temp (°C)': 20.9,
   'Mean Temp (°C)': 16.4,
   'Min Temp (°C)': 11.9,
   'Spd of Max Gust (km/h)': '37',
   'Total Precip (mm)': 0.0,
   'Total Rain (mm)': 0.0,
   'Total Snow (cm)': 0.0}),
 (('w.vic', datetime.date(2013, 7, 12)),
  {'Cool Deg Days (°C)': '0.0',
   'Data Quality': '‡',
   'Dir of Max Gust (10s deg)': '13',
   'Heat Deg Days (°C)': '2.0',
   'Max Temp (°C)': 21.2,
   'Mean Temp (°C)': 16.0,
   'Min Temp (°C)': 10.7,
   'Spd of Max Gust (km/h)': '33',
   'Total Precip (mm)': 0.0,
   'Total Rain (mm)': 0.0,
   'Total Snow (cm)': 0.0}),
 (('w.vic', datetime.date(2013, 7, 13)),
  {'Cool Deg Days (°C)': '0.0',
   'Data Quality': '‡',
   'Dir of Max Gust (10s deg)': '15',
   'Heat Deg Days (°C)': '1.8',
   'Max Temp (°C)': 22.9,
   'Mean Temp (°C)': 16.2,
   'Min Temp (°C)': 9.5,
   'Spd of Max Gust (km

   'Total Snow (cm)': 0.0}),
 (('w.vic', datetime.date(2013, 9, 20)),
  {'Cool Deg Days (°C)': '0.0',
   'Data Quality': '‡',
   'Heat Deg Days (°C)': '4.9',
   'Max Temp (°C)': 19.1,
   'Mean Temp (°C)': 13.1,
   'Min Temp (°C)': 7.1,
   'Spd of Max Gust (km/h)': '<31',
   'Total Precip (mm)': 6.6,
   'Total Rain (mm)': 6.6,
   'Total Snow (cm)': 0.0}),
 (('w.vic', datetime.date(2013, 9, 21)),
  {'Cool Deg Days (°C)': '0.0',
   'Data Quality': '‡',
   'Heat Deg Days (°C)': '4.5',
   'Max Temp (°C)': 17.2,
   'Mean Temp (°C)': 13.5,
   'Min Temp (°C)': 9.8,
   'Spd of Max Gust (km/h)': '<31',
   'Total Precip (mm)': 2.8,
   'Total Rain (mm)': 2.8,
   'Total Snow (cm)': 0.0}),
 (('w.vic', datetime.date(2013, 9, 22)),
  {'Cool Deg Days (°C)': '0.0',
   'Data Quality': '‡',
   'Dir of Max Gust (10s deg)': '15',
   'Heat Deg Days (°C)': '3.9',
   'Max Temp (°C)': 16.9,
   'Mean Temp (°C)': 14.1,
   'Min Temp (°C)': 11.2,
   'Spd of Max Gust (km/h)': '44',
   'Total Precip (mm)': 7.5,
   'T

   'Total Snow (cm)': 0.0}),
 (('w.vic', datetime.date(2013, 11, 23)),
  {'Cool Deg Days (°C)': '0.0',
   'Data Quality': '‡',
   'Heat Deg Days (°C)': '14.5',
   'Max Temp (°C)': 8.4,
   'Mean Temp (°C)': 3.5,
   'Min Temp (°C)': -1.5,
   'Spd of Max Gust (km/h)': '<31',
   'Total Precip (mm)': 0.0,
   'Total Rain (mm)': 0.0,
   'Total Snow (cm)': 0.0}),
 (('w.vic', datetime.date(2013, 11, 24)),
  {'Cool Deg Days (°C)': '0.0',
   'Data Quality': '‡',
   'Heat Deg Days (°C)': '14.2',
   'Max Temp (°C)': 9.4,
   'Mean Temp (°C)': 3.8,
   'Min Temp (°C)': -1.8,
   'Spd of Max Gust (km/h)': '<31',
   'Total Precip (mm)': 0.0,
   'Total Rain (mm)': 0.0,
   'Total Snow (cm)': 0.0}),
 (('w.vic', datetime.date(2013, 11, 25)),
  {'Cool Deg Days (°C)': '0.0',
   'Data Quality': '‡',
   'Heat Deg Days (°C)': '13.5',
   'Max Temp (°C)': 9.2,
   'Mean Temp (°C)': 4.5,
   'Min Temp (°C)': -0.2,
   'Spd of Max Gust (km/h)': '<31',
   'Total Precip (mm)': 0.0,
   'Total Rain (mm)': 0.0,
   'Total Sno

   'Min Temp (°C)': -1.2,
   'Spd of Max Gust (km/h)': '61',
   'Total Precip (mm)': 0.0,
   'Total Rain (mm)': 0.0,
   'Total Snow (cm)': 0.0}),
 (('w.vic', datetime.date(2017, 1, 3)),
  {'Cool Deg Days (°C)': '0.0',
   'Data Quality': '‡',
   'Dir of Max Gust (10s deg)': '6',
   'Heat Deg Days (°C)': '18.9',
   'Max Temp (°C)': 0.5,
   'Mean Temp (°C)': -0.9,
   'Min Temp (°C)': -2.3,
   'Spd of Max Gust (km/h)': '57',
   'Total Precip (mm)': 0.0,
   'Total Rain (mm)': 0.0,
   'Total Snow (cm)': 0.0}),
 (('w.vic', datetime.date(2017, 1, 4)),
  {'Cool Deg Days (°C)': '0.0',
   'Data Quality': '‡',
   'Dir of Max Gust (10s deg)': '6',
   'Heat Deg Days (°C)': '18.2',
   'Max Temp (°C)': 4.1,
   'Mean Temp (°C)': -0.2,
   'Min Temp (°C)': -4.5,
   'Spd of Max Gust (km/h)': '74',
   'Total Precip (mm)': 0.0,
   'Total Rain (mm)': 0.0,
   'Total Snow (cm)': 0.0}),
 (('w.vic', datetime.date(2017, 1, 5)),
  {'Cool Deg Days (°C)': '0.0',
   'Data Quality': '‡',
   'Heat Deg Days (°C)': '19.7

   'Total Rain (mm)': 0.0,
   'Total Snow (cm)': 0.0}),
 (('w.vic', datetime.date(2017, 2, 22)),
  {'Cool Deg Days (°C)': '0.0',
   'Data Quality': '‡',
   'Heat Deg Days (°C)': '15.3',
   'Max Temp (°C)': 7.3,
   'Mean Temp (°C)': 2.7,
   'Min Temp (°C)': -1.9,
   'Spd of Max Gust (km/h)': '<31',
   'Total Precip (mm)': 0.0,
   'Total Rain (mm)': 0.0,
   'Total Snow (cm)': 0.0}),
 (('w.vic', datetime.date(2017, 2, 23)),
  {'Cool Deg Days (°C)': '0.0',
   'Data Quality': '‡',
   'Heat Deg Days (°C)': '15.2',
   'Max Temp (°C)': 6.8,
   'Mean Temp (°C)': 2.8,
   'Min Temp (°C)': -1.3,
   'Spd of Max Gust (km/h)': '<31',
   'Total Precip (mm)': 0.0,
   'Total Rain (mm)': 0.0,
   'Total Snow (cm)': 0.0}),
 (('w.vic', datetime.date(2017, 2, 24)),
  {'Cool Deg Days (°C)': '0.0',
   'Data Quality': '‡',
   'Heat Deg Days (°C)': '15.4',
   'Max Temp (°C)': 6.5,
   'Mean Temp (°C)': 2.6,
   'Min Temp (°C)': -1.4,
   'Spd of Max Gust (km/h)': '<31',
   'Total Precip (mm)': 0.8,
   'Total Rain (

...

   'Snow on Grnd (cm)': '0',
   'Spd of Max Gust (km/h)': '<31',
   'Total Precip (mm)': 3.6,
   'Total Rain (mm)': 3.6,
   'Total Snow (cm)': 0.0}),
 (('w.vic', datetime.date(2012, 4, 25)),
  {'Cool Deg Days (°C)': '0.0',
   'Dir of Max Gust (10s deg)': '28',
   'Dir of Max Gust Flag': 'E',
   'Heat Deg Days (°C)': '6.1',
   'Max Temp (°C)': 14.6,
   'Mean Temp (°C)': 11.9,
   'Min Temp (°C)': 9.1,
   'Snow on Grnd (cm)': '0',
   'Spd of Max Gust (km/h)': '32',
   'Spd of Max Gust Flag': 'E',
   'Total Precip (mm)': 4.0,
   'Total Rain (mm)': 4.0,
   'Total Snow (cm)': 0.0}),
 (('w.vic', datetime.date(2012, 4, 26)),
  {'Cool Deg Days (°C)': '0.0',
   'Dir of Max Gust (10s deg)': '22',
   'Dir of Max Gust Flag': 'E',
   'Heat Deg Days (°C)': '6.9',
   'Max Temp (°C)': 14.6,
   'Mean Temp (°C)': 11.1,
   'Min Temp (°C)': 7.6,
   'Snow on Grnd (cm)': '0',
   'Spd of Max Gust (km/h)': '37',
   'Spd of Max Gust Flag': 'E',
   'Total Precip (mm)': 0.2,
   'Total Rain (mm)': 0.2,
   'Total S

   'Min Temp (°C)': 6.9,
   'Snow on Grnd (cm)': '0',
   'Spd of Max Gust (km/h)': '<31',
   'Total Precip (mm)': 0.0,
   'Total Rain (mm)': 0.0,
   'Total Snow (cm)': 0.0}),
 (('w.vic', datetime.date(2012, 6, 15)),
  {'Cool Deg Days (°C)': '0.0',
   'Heat Deg Days (°C)': '5.9',
   'Max Temp (°C)': 18.7,
   'Mean Temp (°C)': 12.1,
   'Min Temp (°C)': 5.5,
   'Snow on Grnd (cm)': '0',
   'Spd of Max Gust (km/h)': '<31',
   'Total Precip (mm)': 0.0,
   'Total Precip Flag': 'T',
   'Total Rain (mm)': 0.0,
   'Total Rain Flag': 'T',
   'Total Snow (cm)': 0.0}),
 (('w.vic', datetime.date(2012, 6, 16)),
  {'Cool Deg Days (°C)': '0.0',
   'Dir of Max Gust (10s deg)': '12',
   'Dir of Max Gust Flag': 'E',
   'Heat Deg Days (°C)': '2.7',
   'Max Temp (°C)': 19.3,
   'Mean Temp (°C)': 15.3,
   'Min Temp (°C)': 11.3,
   'Snow on Grnd (cm)': '0',
   'Spd of Max Gust (km/h)': '39',
   'Spd of Max Gust Flag': 'E',
   'Total Precip (mm)': 0.6,
   'Total Rain (mm)': 0.6,
   'Total Snow (cm)': 0.0}),
 

   'Total Snow (cm)': 0.0}),
 (('w.vic', datetime.date(2012, 7, 26)),
  {'Cool Deg Days (°C)': '0.0',
   'Heat Deg Days (°C)': '0.6',
   'Max Temp (°C)': 24.0,
   'Mean Temp (°C)': 17.4,
   'Min Temp (°C)': 10.7,
   'Snow on Grnd (cm)': '0',
   'Spd of Max Gust (km/h)': '<31',
   'Total Precip (mm)': 0.0,
   'Total Rain (mm)': 0.0,
   'Total Snow (cm)': 0.0}),
 (('w.vic', datetime.date(2012, 7, 27)),
  {'Cool Deg Days (°C)': '0.0',
   'Heat Deg Days (°C)': '2.2',
   'Max Temp (°C)': 20.1,
   'Mean Temp (°C)': 15.8,
   'Min Temp (°C)': 11.5,
   'Snow on Grnd (cm)': '0',
   'Spd of Max Gust (km/h)': '<31',
   'Total Precip (mm)': 0.0,
   'Total Rain (mm)': 0.0,
   'Total Snow (cm)': 0.0}),
 (('w.vic', datetime.date(2012, 7, 28)),
  {'Cool Deg Days (°C)': '0.0',
   'Heat Deg Days (°C)': '2.8',
   'Max Temp (°C)': 21.0,
   'Mean Temp (°C)': 15.2,
   'Min Temp (°C)': 9.4,
   'Snow on Grnd (cm)': '0',
   'Spd of Max Gust (km/h)': '<31',
   'Total Precip (mm)': 0.0,
   'Total Rain (mm)': 0.0,

   'Total Snow (cm)': 0.0}),
 (('w.vic', datetime.date(2012, 9, 26)),
  {'Cool Deg Days (°C)': '0.0',
   'Heat Deg Days (°C)': '5.7',
   'Max Temp (°C)': 18.0,
   'Mean Temp (°C)': 12.3,
   'Min Temp (°C)': 6.6,
   'Snow on Grnd (cm)': '0',
   'Spd of Max Gust (km/h)': '<31',
   'Total Precip (mm)': 0.0,
   'Total Rain (mm)': 0.0,
   'Total Snow (cm)': 0.0}),
 (('w.vic', datetime.date(2012, 9, 27)),
  {'Cool Deg Days (°C)': '0.0',
   'Heat Deg Days (°C)': '4.0',
   'Max Temp (°C)': 21.3,
   'Mean Temp (°C)': 14.0,
   'Min Temp (°C)': 6.7,
   'Snow on Grnd (cm)': '0',
   'Spd of Max Gust (km/h)': '<31',
   'Total Precip (mm)': 0.0,
   'Total Rain (mm)': 0.0,
   'Total Snow (cm)': 0.0}),
 (('w.vic', datetime.date(2012, 9, 28)),
  {'Cool Deg Days (°C)': '0.0',
   'Heat Deg Days (°C)': '3.9',
   'Max Temp (°C)': 17.6,
   'Mean Temp (°C)': 14.1,
   'Min Temp (°C)': 10.6,
   'Snow on Grnd (cm)': '0',
   'Spd of Max Gust (km/h)': '<31',
   'Total Precip (mm)': 2.0,
   'Total Rain (mm)': 2.0,


   'Heat Deg Days (°C)': '8.5',
   'Max Temp (°C)': 10.6,
   'Mean Temp (°C)': 9.5,
   'Min Temp (°C)': 8.4,
   'Snow on Grnd (cm)': '0',
   'Spd of Max Gust (km/h)': '56',
   'Spd of Max Gust Flag': 'E',
   'Total Precip (mm)': 14.6,
   'Total Rain (mm)': 14.6,
   'Total Snow (cm)': 0.0}),
 (('w.vic', datetime.date(2012, 12, 1)),
  {'Cool Deg Days (°C)': '0.0',
   'Dir of Max Gust (10s deg)': '13',
   'Dir of Max Gust Flag': 'E',
   'Heat Deg Days (°C)': '9.8',
   'Max Temp (°C)': 9.6,
   'Mean Temp (°C)': 8.2,
   'Min Temp (°C)': 6.7,
   'Snow on Grnd (cm)': '0',
   'Spd of Max Gust (km/h)': '46',
   'Spd of Max Gust Flag': 'E',
   'Total Precip (mm)': 21.0,
   'Total Rain (mm)': 21.0,
   'Total Snow (cm)': 0.0}),
 (('w.vic', datetime.date(2012, 12, 2)),
  {'Cool Deg Days (°C)': '0.0',
   'Dir of Max Gust (10s deg)': '14',
   'Dir of Max Gust Flag': 'E',
   'Heat Deg Days (°C)': '9.4',
   'Max Temp (°C)': 10.9,
   'Mean Temp (°C)': 8.6,
   'Min Temp (°C)': 6.2,
   'Snow on Grnd (cm)'

In [53]:
print('length CDD =', len(CDD))
print('length CDTD =', len(CDTD))
print('length CDTPD =', len(CDTPD))

length CDD = 2892
length CDTD = 2683
length CDTPD = 2648


In [54]:
print(CDD, 'crime data days', CDTD, 'crime data + temp days', CDTPD, 'crime data + precipitation + temp days')

[(('w.vic', datetime.date(2013, 1, 1)), {'Data Quality': '‡'}), (('w.vic', datetime.date(2013, 1, 2)), {'Data Quality': '‡'}), (('w.vic', datetime.date(2013, 1, 3)), {'Data Quality': '‡'}), (('w.vic', datetime.date(2013, 1, 4)), {'Data Quality': '‡'}), (('w.vic', datetime.date(2013, 1, 5)), {'Data Quality': '‡'}), (('w.vic', datetime.date(2013, 1, 6)), {'Data Quality': '‡'}), (('w.vic', datetime.date(2013, 1, 7)), {'Data Quality': '‡'}), (('w.vic', datetime.date(2013, 1, 8)), {'Data Quality': '‡'}), (('w.vic', datetime.date(2013, 1, 9)), {'Data Quality': '‡'}), (('w.vic', datetime.date(2013, 1, 10)), {'Data Quality': '‡'}), (('w.vic', datetime.date(2013, 1, 11)), {'Data Quality': '‡'}), (('w.vic', datetime.date(2013, 1, 12)), {'Data Quality': '‡'}), (('w.vic', datetime.date(2013, 1, 13)), {'Data Quality': '‡'}), (('w.vic', datetime.date(2013, 1, 14)), {'Data Quality': '‡'}), (('w.vic', datetime.date(2013, 1, 15)), {'Data Quality': '‡'}), (('w.vic', datetime.date(2013, 1, 16)), {'Data Q

----

## P.4 - Crime + Weather data


1. Find all the days where it was **6°C** warmer than the preceeding 7 days, i.e. the entire preceding week.  Compute the average crime rates for each crime type on these days.  Which crimes were more than twice as common on these days, compared to an average day?

2. Find all the days where it was **6°C** colder than the preceeding 7 days. Compute the average crime rates for each crime type on these days. Which crimes were more than twice as common on these days, compared to an average day?

Use the 'Max Temp (°C)' field for P.4. 

**Grading script** in parts 1 and 2, print your exceptional week weather, one exceptional week per line, in the form:

`2013-05-25 12.2 17.7 12.7 15.0 13.8 14.5 16.6 24.0`

if for example you found that May 25th of 2013 was 24.0c with the weather in the preceding week being the numbers between the date object and the temperature reading on 2013-05-25. 

----

## P.5 - ODEs for polynomials.

In Lecture 8a we developed a differential equation associated to a polynomial whose solutions were either periodic or converged to some of the roots of the polynomial. Specifically, the ODE:

$$\frac{dz}{dt} = iP(z)$$

In this homework assignment we ask you to explore this ODE in more detail.

**(a)** Create a Python function that takes as input a polynomial.  Your function will generate a **basins of attraction plot**, i.e. at each point $z_0$ in the plot you will compute a solution to the above ODE satisfying the initial condition $z(0)=z_0$.  Depending on the behaviour of the solution you will color the point $z_0$ accordingly.  You will choose colours according to each of the roots.  If your solution converges to a root, colour the point $z_0$ accordingly.  Similarly, choose a colour for initial values $z_0$ corresponding to periodic solutions.  And colour the point $z_0$ black if it does neither. 

**(b)**

Include plots for the polynomials:

$$z^3-1$$

$$z^4-1$$

$$z^5-1$$

$$z^5-z-1$$

**(c)** Do your experiments suggest that for any polynomial with real coefficients, the solutions to the above ODE are either periodic or converge to a root?  If so, can you identify which roots are limits of solutions, and which initial values give periodic solutions? 

Note: A polynomial $$c_nz^n + c_{n-1}z^{n-1} + \cdots + c_1 z + c_0$$ is said to have real coefficients if $c_i \in \mathbb R$ for all $i$.